In [1]:
import pandas as pd
import numpy as np
import threading
import time
import queue
import matplotlib.pyplot as plt
from tensorflow import keras
from tensorflow.keras.models import model_from_json

In [2]:
# Lista para guardar las predicciones
history = []

# Parametros de normalización para conjunto TS1-4_COOLER
T_C_0_num = -2304.11053494
T_C_0_den = 7393.278659940001

In [3]:
# Función de normalización
def normalize(x):
  return (x - T_C_0_num) / T_C_0_den

In [4]:
# Logica del proceso Simulador
def simulator(thread_name, console_lock):
    for i in range(len(sds)):
        # Pausa de un segundo entre entregas de datos
        time.sleep(1)
        # Inserción de los datos en el repositorio FIFO
        q.put(sds[i])
        with console_lock:
            print("Proceso Simulador de Lecturas - Proc.Nro. " + str(threading.get_ident()))
            print("Lecturas enviadas: ", sds[i])

In [5]:
# Logica del proceso predictor
def predictor(thread_name, console_lock, loaded_model):
    pred_counter = 0
    serie = np.empty((1, 4))
    while (pred_counter < 912):
        if q.qsize() > 0:
            b = q.get()
            with console_lock:
                print("Proceso Predictor - Proc.Nro. " + str(threading.get_ident()))
                print("Prediccion Nro.: ", pred_counter, " - Datos Recibidos: ", b)
                print("Objetos restantes en la cola: " + str(q.qsize()))
                # Preparado de la Serie
                if pred_counter == 0:
                    serie = np.array([b])
                else:
                    serie = np.append(serie, np.array([b]), axis=0)
                # Grafica de la serie acumulada (Comentado por memoria)
                # plt.plot(serie) (Comentado por memoria)
                # plt.show() (Comentado por memoria)

                # Predicción
                if len(serie) > 0: # Hay suficientes datos para predecir
                    x = normalize(serie[-1:, :])
                    # print("Ultima lectura recibida (Normalizada)")
                    # print(x)
                    pred_val = loaded_model.predict(np.array([x]))
                    i_pred_val = np.argmax(pred_val)
                    history.append(i_pred_val)
                    print("Predicción: ", pred_val, "Etiqueta: ", i_pred_val)
                    print("Estado en 50 segundos: ", text_labels[i_pred_val])
                else:
                    print("No hay suficientes datos para realizar una predicción.")
                pred_counter += 1
        else:
            time.sleep(1)
    # Guardo en archivo el resultado de las predicciones
    mat = np.matrix(history)
    with open('resultados_h_p_s_2.txt', 'wb') as f:
        for line in mat:
            np.savetxt(f, line, fmt='%.4f', delimiter='\t')


In [6]:
# Lectura del dataset sintetico
sds = pd.read_csv('TimeSerie_Real_Data.txt', sep='\t', header=None)
sds = sds.to_numpy()

# Semaforo para acceso a la consola
console_lock = threading.Lock()

# Lectura del modelo de aprendizaje profundo
with open('model_MLP_Real_1.json', 'r') as json_file:
    model_json = json_file.read()
loaded_model = model_from_json(model_json)

# Lectura de los parámetros entrenados
loaded_model.load_weights('model_MLP_Real_1.h5')

# Compilación del modelo
opt = keras.optimizers.Adam(learning_rate=.002)
loaded_model.compile(optimizer = opt, loss='categorical_crossentropy', metrics = ['accuracy'])

# Etiquetas con los estados posibles
text_labels = ['BUEN ESTADO', 'ESTADO CRITICO']

# Creación del repositorio para intercambio de datos entre procesos (FIFO)
q = queue.Queue()

# Visualización de la estructura del modelo de aprendizaje profundo leido
loaded_model.summary()

# Creación de los procesos concurrentes
p1 = threading.Thread(target=simulator, args=('p1', console_lock))
p2 = threading.Thread(target=predictor, args=('p2', console_lock, loaded_model))

# Inicio de la ejecución de los procesos
p1.start()
p2.start()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 140)               16800     
_________________________________________________________________
dense_1 (Dense)              (None, 50)                7050      
_________________________________________________________________
dense_2 (Dense)              (None, 2)                 102       
Total params: 23,952
Trainable params: 23,952
Non-trainable params: 0
_________________________________________________________________
Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 4.5810400e+01  1.0095800e+01  5.4988100e+01  7.4557400e+01
  6.1034940e+02  3.2955600e+01  9.7919000e+00  1.8515080e+02
  5.0000000e-04  6.6868000e+01  1.2499500e+02  8.2069000e+00
  6.6001100e+01  1.6867080e+02  2.0270100e+01  1.6379010e+02
  1.8362400e+02  7.0475900e+01 -6.8991000e+00  3.1032000e+00
  1.63923

Predicción:  [[[0.9785791  0.02142091]]] Etiqueta:  0
Estado en 50 segundos:  BUEN ESTADO
Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 4.6347600e+01  9.9507000e+00  5.6404900e+01  7.5803500e+01
  6.1002980e+02  3.4022900e+01  9.9191000e+00  1.8494660e+02
  5.0000000e-04  6.7923700e+01  1.2467470e+02  8.0646000e+00
  6.6083500e+01  1.7055960e+02  2.1444100e+01  1.6429360e+02
  1.8341100e+02  7.0458700e+01 -6.8991000e+00  3.0908000e+00
  1.5530700e+01  6.9001000e+00  1.6027000e+00  7.1537900e+01
  1.4259000e+00  1.4880000e+00  9.0084500e+01  6.2288500e+01
  1.2724000e+00  1.1932000e+00  1.5691000e+00  1.3479000e+00
  1.5211490e+02  8.1790000e-01  8.1930000e-01 -2.2451547e+03
  2.0629260e+02  1.5777000e+00  1.3347000e+00  2.1174160e+03
  4.3807828e+03  1.8481450e+02  1.3807000e+00  1.3720000e+00
  7.9979000e+00  7.4088000e+00  1.7150000e+00  1.4580000e-01
  3.2617400e+01  5.2693330e+02  5.1913080e+02  5.1529880e+02
  5.1574680e+02  5.1602170e+02  3.3027300e+01  3.

Proceso Predictor - Proc.Nro. 11132
Prediccion Nro.:  4  - Datos Recibidos:  [ 4.6635000e+01  9.7774000e+00  5.7186600e+01  7.5569200e+01
  6.1030530e+02  3.3893600e+01  1.0024500e+01  1.8495530e+02
  5.0000000e-04  6.8035500e+01  1.2495080e+02  8.2282000e+00
  6.6023800e+01  1.6990000e+02  2.1640300e+01  1.6392190e+02
  1.8333310e+02  7.0405200e+01 -6.8991000e+00  3.0982000e+00
  1.5481800e+01  6.9013000e+00  1.6001000e+00  7.1503100e+01
  1.4300000e+00  1.4933000e+00  8.9269700e+01  6.1852200e+01
  1.2798000e+00  1.1966000e+00  1.5751000e+00  1.3504000e+00
  1.5237780e+02  8.1820000e-01  8.1990000e-01 -2.2524192e+03
  2.0315030e+02  1.5841000e+00  1.3416000e+00  2.1855278e+03
  4.3509311e+03  1.8481450e+02  1.3831000e+00  1.3744000e+00
  7.9976000e+00  7.3996000e+00  1.7199000e+00  1.4480000e-01
  3.2548000e+01  5.2610000e+02  5.1901050e+02  5.1506920e+02
  5.1550720e+02  5.1575810e+02  3.3290900e+01  3.3044300e+01
  1.1064380e+02  9.0079700e+01  1.3624360e+02  1.3480740e+02
  2.1468

Predicción:  [[[0.98103416 0.01896591]]] Etiqueta:  0
Estado en 50 segundos:  BUEN ESTADO
Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 4.6542700e+01  9.6954000e+00  5.8909400e+01  7.4287700e+01
  6.1015680e+02  3.5459400e+01  1.0070400e+01  1.8519410e+02
  5.0000000e-04  6.7729400e+01  1.2517410e+02  8.0550000e+00
  6.6116300e+01  1.7285890e+02  2.1345500e+01  1.6407730e+02
  1.8385170e+02  7.0516800e+01 -6.8991000e+00  3.1540000e+00
  1.6908400e+01  6.9042000e+00  1.5987000e+00  7.1581300e+01
  1.4156000e+00  1.4779000e+00  8.9164900e+01  6.2894300e+01
  1.2646000e+00  1.1830000e+00  1.5528000e+00  1.3330000e+00
  1.4978430e+02  8.1640000e-01  8.1990000e-01 -2.2507050e+03
  2.0527860e+02  1.5685000e+00  1.3276000e+00  2.1756028e+03
  4.2939781e+03  1.8481450e+02  1.3657000e+00  1.3575000e+00
  8.0004000e+00  7.3995000e+00  1.7042000e+00  1.5180000e-01
  3.2742900e+01  5.2636670e+02  5.1857720e+02  5.1447590e+02
  5.1494100e+02  5.1519610e+02  3.3239300e+01  3.

Predicción:  [[[0.9785558  0.02144416]]] Etiqueta:  0
Estado en 50 segundos:  BUEN ESTADO
Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 4.6240100e+01  9.8407000e+00  5.9481500e+01  7.4193000e+01
  6.0982000e+02  3.4677200e+01  1.0151600e+01  1.8604670e+02
  5.0000000e-04  7.0504700e+01  1.2485190e+02  8.1281000e+00
  6.5762500e+01  1.7444910e+02  2.1728400e+01  1.6397660e+02
  1.8449270e+02  7.0951000e+01 -6.8991000e+00  3.2617000e+00
  1.6717200e+01  6.8896000e+00  1.6008000e+00  7.1997800e+01
  1.4246000e+00  1.4893000e+00  9.0262000e+01  6.2961100e+01
  1.2829000e+00  1.1909000e+00  1.5574000e+00  1.3429000e+00
  1.5017090e+02  8.1580000e-01  8.1990000e-01 -2.1570226e+03
  2.0629240e+02  1.5792000e+00  1.3459000e+00  2.1024122e+03
  4.1862175e+03  1.8481450e+02  1.3734000e+00  1.3666000e+00
  8.0001000e+00  7.4004000e+00  1.7106000e+00  1.5340000e-01
  3.0403800e+01  5.2638440e+02  5.1903570e+02  5.1508630e+02
  5.1548590e+02  5.1578940e+02  3.2628100e+01  3.

...

Proceso Predictor - Proc.Nro. 11132
Prediccion Nro.:  899  - Datos Recibidos:  [ 5.2019800e+01  1.1334300e+01  5.1958800e+01  7.0385200e+01
  5.0014420e+02  3.0217700e+01  9.2750000e+00  1.4604720e+02
  7.2970000e-01  5.8072000e+01  9.3044500e+01  8.1018000e+00
  4.7155300e+01  1.4316730e+02  2.3415100e+01  1.4163400e+02
  1.4711540e+02  6.7084700e+01 -4.0000000e-04  2.8920000e+00
  2.7461000e+00  7.4695000e+00  1.6011000e+00  7.0005500e+01
  1.4365000e+00  1.4880000e+00  6.8698000e+01  5.3827400e+01
  1.3343000e+00  1.2269000e+00  1.5894000e+00  1.3669000e+00
  1.3987550e+02  8.5860000e-01  8.6090000e-01 -1.4952632e+03
  1.9258120e+02  1.5571000e+00  1.3885000e+00  2.2289332e+03
  3.9155360e+03  1.8481450e+02  1.3928000e+00  1.3861000e+00
  7.9992000e+00  8.0992000e+00  1.7305000e+00  1.4070000e-01
  2.5934700e+01  5.3839330e+02  5.3360090e+02  5.2842840e+02
  5.2921600e+02  5.2942300e+02  2.9830400e+01  2.9557800e+01
  1.0975470e+02  8.4827800e+01  1.3459520e+02  1.3383240e+02
  2.20

Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 4.2774500e+01  1.0114400e+01  5.3151600e+01  6.8560300e+01
  5.0094510e+02  2.8258500e+01  9.3941000e+00  1.4608890e+02
  3.2068000e+00  7.2889700e+01  9.2846000e+01  8.0827000e+00
  4.7113900e+01  1.5105570e+02  2.1879000e+01  1.4319770e+02
  1.4423840e+02  6.7286900e+01 -4.0000000e-04  3.2046000e+00
  2.3100000e-01  7.4771000e+00  1.6001000e+00  6.9719900e+01
  1.3797000e+00  1.4307000e+00  6.7082600e+01  5.5630100e+01
  1.2747000e+00  1.1811000e+00  1.5220000e+00  1.3090000e+00
  1.3189520e+02  8.5610000e-01  8.5970000e-01 -1.5518205e+03
  1.9309980e+02  1.4981000e+00  1.3302000e+00  2.2477224e+03
  3.8927214e+03  1.8481450e+02  1.3333000e+00  1.3268000e+00
  7.7001000e+00  8.1009000e+00  1.6747000e+00  1.5240000e-01
  2.4330500e+01  5.2588890e+02  5.2533230e+02  5.2075180e+02
  5.2169750e+02  5.2168760e+02  3.0253500e+01  2.9666800e+01
  1.0915230e+02  8.6847000e+01  1.3231860e+02  1.3151130e+02
  2.2049250e+02  

Proceso Predictor - Proc.Nro. 11132
Prediccion Nro.:  904  - Datos Recibidos:  [ 3.7070000e+01  1.0867500e+01  5.1615800e+01  6.8804000e+01
  5.0014890e+02  2.8754400e+01  9.3795000e+00  1.4596710e+02
  4.1164000e+00  7.2612100e+01  9.2945300e+01  7.9019000e+00
  4.4885400e+01  1.5713340e+02  2.1256300e+01  1.4699820e+02
  1.4428980e+02  6.7466500e+01 -4.0000000e-04  3.2020000e+00
  8.8269000e+00  7.5366000e+00  1.5993000e+00  6.9837300e+01
  1.3733000e+00  1.4281000e+00  6.9236000e+01  5.6510200e+01
  1.2769000e+00  1.1788000e+00  1.4999000e+00  1.3075000e+00
  1.2739170e+02  8.5300000e-01  8.5930000e-01 -1.5501135e+03
  1.9364730e+02  1.4961000e+00  1.3331000e+00  2.2104520e+03
  3.8589964e+03  1.8481450e+02  1.3326000e+00  1.3260000e+00
  7.7031000e+00  8.1028000e+00  1.6823000e+00  1.8250000e-01
  2.5171700e+01  5.2233550e+02  5.2276270e+02  5.1855510e+02
  5.1953830e+02  5.1961660e+02  2.9594800e+01  2.9139400e+01
  1.1068410e+02  9.0246100e+01  1.3257870e+02  1.3164020e+02
  2.20

Predicción:  [[[0.11967114 0.8803289 ]]] Etiqueta:  1
Estado en 50 segundos:  ESTADO CRITICO
Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 3.7502300e+01  1.0917400e+01  5.2596000e+01  6.7946800e+01
  4.9916120e+02  3.1545600e+01  9.3843000e+00  1.4594270e+02
  5.0220000e+00  7.0241000e+01  9.2985300e+01  8.0538000e+00
  4.5776000e+01  1.5695860e+02  2.1413900e+01  1.5265890e+02
  1.4469270e+02  6.7387000e+01 -4.0000000e-04  3.1935000e+00
  7.2279000e+00  7.5212000e+00  1.5982000e+00  6.9838100e+01
  1.3720000e+00  1.4227000e+00  6.8614900e+01  5.6003500e+01
  1.2733000e+00  1.1764000e+00  1.4978000e+00  1.3043000e+00
  1.2796180e+02  8.5450000e-01  8.5970000e-01 -1.5593113e+03
  1.9568640e+02  1.4911000e+00  1.3290000e+00  2.2566179e+03
  3.8436204e+03  1.8481450e+02  1.3313000e+00  1.3223000e+00
  7.6968000e+00  8.0967000e+00  1.6763000e+00  1.7850000e-01
  2.6866500e+01  5.2357790e+02  5.2345700e+02  5.1892820e+02
  5.1997690e+02  5.2005510e+02  2.9443300e+01 

Proceso Simulador de Lecturas - Proc.Nro. 12492
Lecturas enviadas:  [ 4.2034100e+01  1.0474900e+01  5.1293800e+01  6.6508600e+01
  4.9976110e+02  2.9165600e+01  9.4664000e+00  1.4601730e+02
  5.1841000e+00  6.9575900e+01  9.2763800e+01  8.1408000e+00
  4.4952300e+01  1.5321920e+02  1.9499100e+01  1.5477290e+02
  1.4637440e+02  6.7932400e+01 -4.0000000e-04  3.2030000e+00
  1.0786200e+01  7.4951000e+00  1.6002000e+00  6.9765300e+01
  1.3395000e+00  1.3919000e+00  6.9588300e+01  5.7360000e+01
  1.2117000e+00  1.1446000e+00  1.4685000e+00  1.2721000e+00
  1.2567470e+02  8.5820000e-01  8.5950000e-01 -1.7811447e+03
  1.9575550e+02  1.4612000e+00  1.2688000e+00  2.1228711e+03
  3.9685239e+03  1.8481450e+02  1.2990000e+00  1.2927000e+00
  7.6997000e+00  8.5571000e+00  1.6457000e+00  1.7730000e-01
  2.6439700e+01  5.2500670e+02  5.2029990e+02  5.1685640e+02
  5.1771850e+02  5.1800140e+02  2.7644500e+01  2.8734300e+01
  1.1089230e+02  9.1181700e+01  1.3250870e+02  1.3150370e+02
  2.2034330e+02  